### V1

In [1]:
import pandas as pd
import altair as alt
alt.data_transformers.enable("vegafusion")
import numpy as np
import matplotlib.pyplot as plt

In [3]:
def preprocess(df):
    # Renommer les colonnes pour plus de clarté
    df = df.rename(columns={"preusuel": "prénom", "annais": "année"})

    # Supprimer les lignes avec des prénoms rares ou des années invalides
    df = df[df["prénom"] != "_PRENOMS_RARES"]
    df = df[df["année"] != "XXXX"]

    # Séparer les données en deux DataFrames selon le sexe
    df_boy = df[df["sexe"] == 1]
    df_girl = df[df["sexe"] == 2]
    
    # Supprimer les colonnes non utilisées
    df_boy = df_boy.drop(columns=["sexe", "dpt"])
    df_girl = df_girl.drop(columns=["sexe", "dpt"])

    # Calculer le nombre total d’occurrences de chaque prénom
    df_boy_grp = df_boy.groupby("prénom")["nombre"].sum().reset_index()
    df_girl_grp = df_girl.groupby("prénom")["nombre"].sum().reset_index()

    # Réduire progressivement le nombre de prénoms en supprimant les moins fréquents (jusqu'à 50)
    occ = 10
    while len(df_boy_grp) > 50 or len(df_girl_grp) > 50:
        # Filtrer les prénoms avec le plus d'occurrences
        df_boy_grp = df_boy_grp[df_boy_grp["nombre"] > occ]
        df_girl_grp = df_girl_grp[df_girl_grp["nombre"] > occ]

        # Recalculer les prénoms communs après filtrage
        common_names = list(set(df_boy_grp["prénom"]) & set(df_girl_grp["prénom"]))

        # Garder seulement les prénoms communs dans les groupes
        df_boy_grp = df_boy_grp[df_boy_grp["prénom"].isin(common_names)]
        df_girl_grp = df_girl_grp[df_girl_grp["prénom"].isin(common_names)]

        occ += 10  # Augmenter le seuil pour resserrer encore

    # Filtrer les DataFrames d’origine pour ne garder que les prénoms communs
    df_boy = df_boy[df_boy["prénom"].isin(common_names)]
    df_girl = df_girl[df_girl["prénom"].isin(common_names)]

    # Convertir les années en entiers
    df_boy["année"]  = df_boy["année"].astype(int)
    df_girl["année"] = df_girl["année"].astype(int)

    # Ajouter une colonne "genre" pour les différencier dans les visualisations
    df_boy["genre"]  = "Homme"
    df_girl["genre"] = "Femme"

    # Fusionner les deux DataFrames et agréger les occurrences
    df_all = pd.concat([df_boy, df_girl], ignore_index=True)
    df_all = df_all.groupby(["année", "prénom", "genre"], as_index=False)["nombre"].sum()

    # Générer un index multi-dimensionnel avec toutes les combinaisons possibles année/prénom/genre
    years   = np.unique(df_all["année"])
    genders = ["Homme", "Femme"]
    mi = pd.MultiIndex.from_product([years, common_names, genders], names=["année", "prénom", "genre"])

    # Reindexer le DataFrame pour combler les valeurs manquantes (remplies avec 0)
    df_all = df_all.set_index(["année", "prénom", "genre"]).reindex(mi, fill_value=0).reset_index()

    # Appliquer une symétrie verticale en inversant les valeurs féminines (pour affichage miroir)
    df_all.loc[df_all["genre"] == "Femme", "nombre"] *= -1

    # Calculer la valeur logarithmique signée (log miroir)
    df_all["log_nombre"] = np.log10(df_all["nombre"].abs() + 1) * np.sign(df_all["nombre"])

    return df_all, common_names, years, genders  # Retourner le DataFrame prêt pour Altair et la liste des noms communs, années et genres


In [4]:
# Lecture du dataset
df = pd.read_csv("../datas/dpt2020.csv", sep=";")

# Preprocessing
df_all, common_names, years, genders = preprocess(df)

In [5]:
# Définition du slider année
year_param = alt.param(name="Année", bind=alt.binding_range(min=years.min(), max=years.max(), step=1), value=1900)

# Calcul de la borne max absolue du log pour fixer l’axe
max_log = df_all["log_nombre"].abs().max()

labelFontSize=16    # taille des étiquettes
titleFontSize=18

# Construiction du Chart
chart = (
    alt.Chart(df_all)
    .mark_bar()
    .encode(
        x=alt.X(
            "prénom:N",
            sort=common_names,
            axis=alt.Axis(labelAngle=45, title="Prénom",
                          labelFontSize=labelFontSize, titleFontSize=titleFontSize)
        ),
        y=alt.Y(
            "log_nombre:Q",
            scale=alt.Scale(domain=[-max_log, max_log]),
            axis=alt.Axis(title="log() (↑Homme, ↓Femme)",
                          labelFontSize=labelFontSize, titleFontSize=titleFontSize)
        ),
        color=alt.Color(
            "genre:N",
            scale=alt.Scale(domain=genders,
                            range=["steelblue","lightpink"]),
            legend=alt.Legend(title="Genre",
                              titleFontSize=titleFontSize, labelFontSize=labelFontSize)
        ),
        tooltip=[
            alt.Tooltip("prénom:N",    title="Prénom"),
            alt.Tooltip("nombre:Q",     title="Nombre brut"),
            alt.Tooltip("log_nombre:Q", title="Log()×signe")
        ]
    )
    .add_params(year_param)
    .transform_filter(alt.datum.année == year_param)
    .properties(
        width=1500,
        height=900,
        title=alt.TitleParams(
            text="Répartition (log) des prénoms par année",
            fontSize=titleFontSize
        )
    )
)

# Affichage du chart
chart

alt.Chart(...)

# Idées : 
- sort (réussir) les prénoms sur l'axe x
- proposer une visulisation de la différence (positive ou négative) de chaque prénom par rapport à l'année précédente
- étendre la proposition précédente à une visualisation sur 5, 10 ou 20 ans

### V2

In [ ]:
def preprocess(df):
    # Rename columns for clarity
    df = df.rename(columns={"preusuel": "name", "annais": "year", "nombre": "number"})

    # Remove rows with rare names or invalid years
    df = df[df["name"] != "_PRENOMS_RARES"]
    df = df[df["year"] != "XXXX"]

    # Split data into two DataFrames based on gender
    df_boy = df[df["sexe"] == 1]
    df_girl = df[df["sexe"] == 2]

    # Drop unused columns
    df_boy = df_boy.drop(columns=["sexe", "dpt"])
    df_girl = df_girl.drop(columns=["sexe", "dpt"])

    # Calculate total occurrences of each name
    df_boy_grp = df_boy.groupby("name")["number"].sum().reset_index()
    df_girl_grp = df_girl.groupby("name")["number"].sum().reset_index()

    # Iteratively filter out less common names until only the top 50 remain
    occ = 10
    while len(df_boy_grp) > 50 or len(df_girl_grp) > 50:
        # Keep names with more than 'occ' occurrences
        df_boy_grp = df_boy_grp[df_boy_grp["number"] > occ]
        df_girl_grp = df_girl_grp[df_girl_grp["number"] > occ]

        # Find common names in both groups
        common_names = list(set(df_boy_grp["name"]) & set(df_girl_grp["name"]))

        # Keep only common names
        df_boy_grp = df_boy_grp[df_boy_grp["name"].isin(common_names)]
        df_girl_grp = df_girl_grp[df_girl_grp["name"].isin(common_names)]

        occ += 10  # Increase threshold to filter further if needed

    # Filter the original DataFrames to only keep common names
    df_boy = df_boy[df_boy["name"].isin(common_names)]
    df_girl = df_girl[df_girl["name"].isin(common_names)]

    # Convert 'year' to integer
    df_boy["year"] = df_boy["year"].astype(int)
    df_girl["year"] = df_girl["year"].astype(int)

    # Add a 'gender' column for visualization purposes
    df_boy["gender"] = "Male"
    df_girl["gender"] = "Female"

    # Merge both DataFrames and aggregate occurrences
    df_all = pd.concat([df_boy, df_girl], ignore_index=True)
    df_all = df_all.groupby(["year", "name", "gender"], as_index=False)["number"].sum()

    # Create a complete multi-index of all year/name/gender combinations
    years = np.unique(df_all["year"])
    genders = ["Male", "Female"]
    mi = pd.MultiIndex.from_product([years, common_names, genders], names=["year", "name", "gender"])

    # Reindex to fill missing values with 0
    df_all = df_all.set_index(["year", "name", "gender"]).reindex(mi, fill_value=0).reset_index()

    # Apply vertical mirroring: invert female values for mirrored display
    df_all.loc[df_all["gender"] == "Female", "number"] *= -1

    return df_all, common_names, years, genders


In [13]:
# Dataset reading
df = pd.read_csv("../datas/dpt2020.csv", sep=";")

# Preprocessing
df_all, common_names, years, genders = preprocess(df)

In [6]:
# S'assurer que les données sont triées
df_all = df_all.sort_values(by=["prénom", "genre", "année"]).reset_index(drop=True)

# Création de la colonne variation sous forme de liste
variations_list = []

# Parcourir chaque ligne
for idx, row in df_all.iterrows():
    prénom = row["prénom"]
    genre   = row["genre"]
    année_courante = row["année"]
    
    # Sous-ensemble avec le même prénom ET le même genre
    subset = df_all[
        (df_all["prénom"] == prénom) &
        (df_all["genre"] == genre)
    ]
    
    # Liste pour stocker les variations sur 1 à 100 ans en arrière
    var_list = []
    for k in range(1, 101):
        année_passée = année_courante - k
        past_row = subset[subset["année"] == année_passée]
        
        if not past_row.empty:
            var = row["nombre"] - past_row["nombre"].values[0]
        else:
            var = 0
        var_list.append(var)
    
    variations_list.append(var_list)

# Ajout de la colonne dans le dataframe
df_all["variation"] = variations_list


In [14]:
# Make sure the data is sorted
df_all = df_all.sort_values(by=["name", "gender", "year"]).reset_index(drop=True)

# Create the 'variation' column as a list
variations_list = []

# Loop over each row
for idx, row in df_all.iterrows():
    name = row["name"]
    gender = row["gender"]
    current_year = row["year"]
    
    # Subset with the same name AND the same gender
    subset = df_all[
        (df_all["name"] == name) &
        (df_all["gender"] == gender)
    ]
    
    # List to store variations over 1 to 100 years back
    var_list = []
    for k in range(1, 101):
        past_year = current_year - k
        past_row = subset[subset["year"] == past_year]
        
        if not past_row.empty:
            var = row["number"] - past_row["number"].values[0]
        else:
            var = 0  # If there is no data for the past year
        var_list.append(var)
    
    variations_list.append(var_list)

# Add the 'variation' column to the dataframe
df_all["variation"] = variations_list


In [16]:
# Year slider definition
year_param = alt.param(name="Year", bind=alt.binding_range(min=years.min(), max=years.max(), step=1), value=1900)
k_param = alt.param(name="k", bind=alt.binding_range(min=1, max=100, step=1), value=1)

# Maximum bounds for scaling
B = df_all["number"].abs().max()

# Scaling definition using symmetrical logarithmic scale
y_scale = alt.Scale(type="symlog", domain=[-B, B])

# Text sizes
labelFontSize = 16
titleFontSize = 18

# Hover selection (mouseover on name)
hover = alt.selection_point(
    name="hover",
    on="mouseover",
    fields=["name"],
    empty="none"
)

# Base chart with filters and calculated fields
base = (
    alt.Chart(df_all)
    .add_params(year_param, k_param)
    .transform_filter(alt.datum.year == year_param)
    .transform_calculate(
        # Variation over k years
        var_k="datum.variation[k - 1]",
        # Previous value
        past="datum.number - datum.variation[k - 1]",
        # Expose k value for tooltip
        k_label="k",
        # Compute front/back bar depending on gender
        front_val="""
        if(
            datum.gender == 'Male',
            if(datum.past <= datum.number, datum.past, datum.number),
            if(datum.past >= datum.number, datum.past, datum.number)
        )
        """,
        back_val="""
        if(
            datum.gender == 'Male',
            if(datum.past > datum.number, datum.past, datum.number),
            if(datum.past < datum.number, datum.past, datum.number)
        )
        """
    )
)

# Current year bars
current_bars = base.mark_bar().encode(
    x=alt.X(
        "name:N",
        sort=common_names,
        axis=alt.Axis(labelAngle=45, title="Name",
                      labelFontSize=labelFontSize, titleFontSize=titleFontSize)
    ),
    y=alt.Y(
        "number:Q",
        scale=y_scale,
        axis=alt.Axis(title="symlog() (↑Male, ↓Female)",
                      labelFontSize=labelFontSize, titleFontSize=titleFontSize)
    ),
    color=alt.Color(
        "gender:N",
        scale=alt.Scale(domain=genders,
                        range=["steelblue", "lightpink"]),
        legend=alt.Legend(title="Gender",
                           titleFontSize=titleFontSize, labelFontSize=labelFontSize)
    ),
    tooltip=[
        alt.Tooltip("name:N", title="Name"),
        alt.Tooltip("number:Q", title="Raw number"),
    ]
).add_params(hover)

# Back bar representing the difference (variation)
back_bars = base.mark_bar().encode(
    x=alt.X("name:N", sort=common_names,
            axis=alt.Axis(labelAngle=45, title="Name",
                          labelFontSize=labelFontSize, titleFontSize=titleFontSize)),
    y=alt.Y("back_val:Q",
            scale=y_scale,
            axis=alt.Axis(title="symlog() (↑Male, ↓Female)",
                          labelFontSize=labelFontSize, titleFontSize=titleFontSize)),
    color=alt.condition(
        # For males: green if current > past; for females: green if current < past
        "(datum.gender == 'Male' && datum.number > datum.past) " +
        "|| (datum.gender != 'Male' && datum.number < datum.past)",
        alt.value("green"),
        alt.value("red")
    ),
    opacity=alt.condition(hover, alt.value(0.6), alt.value(0)),
    tooltip=[
        alt.Tooltip("name:N", title="Name"),
        alt.Tooltip("number:Q", title="Current number"),
        alt.Tooltip("var_k:Q", title="Variation"),
    ]
)

# Front bar representing the smallest value (before or after)
front_bars = base.mark_bar().encode(
    x=alt.X(
        "name:N",
        sort=common_names,
        axis=alt.Axis(labelAngle=45, title="Name",
                      labelFontSize=labelFontSize, titleFontSize=titleFontSize)
    ),
    y=alt.Y(
        "front_val:Q",
        scale=y_scale,
        axis=alt.Axis(title="symlog() (↑Male, ↓Female)",
                      labelFontSize=labelFontSize, titleFontSize=titleFontSize)
    ),
    color=alt.Color(
        "gender:N",
        scale=alt.Scale(domain=genders,
                        range=["steelblue", "lightpink"]),
        legend=alt.Legend(title="Gender",
                           titleFontSize=titleFontSize, labelFontSize=labelFontSize)
    ),
    opacity=alt.condition(hover, alt.value(0.6), alt.value(0)),
    tooltip=[
        alt.Tooltip("name:N", title="Name"),
        alt.Tooltip("number:Q", title="Current number"),
        alt.Tooltip("var_k:Q", title="Variation"),
    ]
)

# Zero line for the y-axis
zero_line = (
    base
    .transform_calculate(zero="0")
    .mark_rule(color="black", strokeWidth=1)
    .encode(
        y=alt.Y("zero:Q")
    )
)

# Combine layers into a single chart
chart = (
    alt.layer(current_bars, back_bars, front_bars, zero_line)
    .properties(
        width=1500,
        height=900,
        title=alt.TitleParams(
            text="Distribution (symlog) of the 50 most common names per year with variation over k year(s)",
            fontSize=titleFontSize
        )
    )
)

chart


alt.LayerChart(...)